# Libraries

In [1]:
from utils import *
from pprint import pprint
import pandas as pd
from spellchecker import SpellChecker
spell = SpellChecker()

import pickle

import ssl
ssl._create_default_https_context = ssl._create_unverified_context

config = get_config('config.yaml')

[nltk_data] Error loading stopwords: <urlopen error [WinError 10060] A
[nltk_data]     connection attempt failed because the connected party
[nltk_data]     did not properly respond after a period of time, or
[nltk_data]     established connection failed because connected host
[nltk_data]     has failed to respond>


# Read Input

In [2]:
df = pd.read_csv(config['csv_input_local']['all_reviews'], index_col=0)
df = df.reset_index(drop=True)
total_reviews = len(df)
unique_users  = len(df['userName'].unique())
mean = df['rating'].mean()

print(f'Total English reviews: {total_reviews} \n')
print(f'Total unique users : {unique_users}')
print(f'Total users who gave multiple reviews: {total_reviews - unique_users}\n')
print(f'Average rating for this app based on the textual reviews: {round(mean,2)} \n')

Total English reviews: 182361 

Total unique users : 171058
Total users who gave multiple reviews: 11303

Average rating for this app based on the textual reviews: 3.64 



# Preprocessing Input Data

## Remove Non-English User Reviews

In [5]:
%%time
listOfNonEnglishIndex = []

for i in range(0, len(df)):
    reviewText = df['review'][i]
    
#     # for debugging purpose
#     print(reviewText)
#     print(isEnglishReview(reviewText))
#     print('\n')
    
    isEnglish, listToStr, english_score = isEnglishReview(reviewText)
    if isEnglish == False:
        listOfNonEnglishIndex.append(i)

Wall time: 20min 57s


In [6]:
%%time
df_p1 = df.drop(df.index[listOfNonEnglishIndex])
total_reviews_before = len(df)
total_reviews_after = len(df_p1)
total_non_english_reviews = len(listOfNonEnglishIndex)

print(f'Total reviews (BEFORE): {total_reviews_before} \n')
print(f'Total reviews (AFTER): {total_reviews_after} \n')
print(f'Total Non-English reviews: {total_non_english_reviews} \n')

Total reviews (BEFORE): 182361 

Total reviews (AFTER): 108084 

Total Non-English reviews: 74277 

Wall time: 38.4 ms


In [7]:
df_p1.to_csv(config['csv_input_local']['all_reviews_p1'])

## Filtering Out Inconsistent User Review

- Because of an issue in SentiStrength path setting for Windows 10, I can't run it here
- Will able to run it via Linux or macOS

In [7]:
df_p2 = pd.read_csv(config['csv_input_local']['all_reviews_p2'], index_col=0)
df_p2 = df_p2.reset_index(drop=True)
df_p2

userName                                             review  \
0          Hilary Meyer  Your drivers are great BUT your support is no ...   
1             Kenneth B  Loving the app, but can only give it a medium ...   
2      Bonolo Mphahlele  The response time with regards to customer ser...   
3       jessfechi egolo  This has been happening for some time now and ...   
4         Safeeya Lawal  The drivers almost always never have change an...   
...                 ...                                                ...   
47407           Mihkelp  It’s just terrible app, doesn’t function prope...   
47408       Nikolas4553                   Very shameful navigation system.   
47409     lalalaaalalaa  taxis are always late without exception. drive...   
47410              Av1K  Cant activate. Only 3 language , not 16 langua...   
47411          tln🤬🤬🤬🤬🤬                              Geolocation is awful.   

       rating                 date  
0           3  2020-12-06 19:38:13  
1           3  2020-12-11 14:06:15  
2           4  2020-12-07 13:59:18  
3           1  2020-12-13 18:19:06  
4           3  2020-12-05 15:08:10  
...       ...                  ...  
47407       1  2018-05-04 20:40:34  
47408       1  2020-06-12 19:10:34  
47409       1  2020-11-07 15:30:33  
47410       1  2018-05-02 00:50:25  
47411       1  2020-10-03 06:03:02  

[47412 rows x 4 columns]

In [24]:
total_reviews_before = len(df_p1)
total_reviews_after = len(df_p2)
total_removed_reviews = total_reviews_before - total_reviews_after

print(f'Total reviews (BEFORE): {total_reviews_before} \n')
print(f'Total reviews (AFTER): {total_reviews_after} \n')
print(f'Total Removed reviews: {total_removed_reviews} \n')

Total reviews (BEFORE): 108084 

Total reviews (AFTER): 47412 

Total Removed reviews: 60672 



## Filtering Out Uninformative Reviews

In [2]:
%run ./AR_Miner/AR_util.py
%run ./AR_Miner/AR_reviewInstance.py

# Inputs:
datasetName = "all" # four apps: facebook, templerun2, swiftkey, tapfish:
rmStopWords = True # Removing stop words lead to information loss and bad f-score
rmRareWords = True # Remove the word with low frequency
skParse = False # set skParse True to directly read of the data that has been filtered out

# Outputs:
if(skParse == False):
    trainSet, testSet, unlabelSet, vocabulary = AR_parse(datasetName, rmStopWords, rmRareWords)

print('\n')

./datasets/_thesis/trainU\all.csv
Vocabulary size for all : 6561
Training set Size: 1447
Testing set Size: 2067
Unlabeling set Size: 47412




In [10]:
# for i in range(0, len(unlabelSet)):
#     print(unlabelSet[i].id)

In [3]:
%%time
%run ./AR_Miner/AR_classifier.py

useSVM = True # SVM is way better than EMNB in the testing
if(skParse == False):
    if(useSVM == False):
#         informRev, informMat = AR_emnb(trainSet, testSet, unlabelSet, vocabulary, datasetName)
        informRev, uninformRev, informMat = AR_emnb(trainSet, testSet, unlabelSet, vocabulary, datasetName)
    else:
#         informRev, informMat = AR_svm(trainSet, testSet, unlabelSet, vocabulary, datasetName)
        informRev, uninformRev, informMat = AR_svm(trainSet, testSet, unlabelSet, vocabulary, datasetName)
    # write the result back to the file (optional)
    # AR_writeReviews(informRev, datasetName)
    
else:
    # directly read from the file
    informRev, informMat, vocabulary = AR_loadReviews(datasetName)

print("Number of informative reviews: " + str(len(informRev)))
print("Number of uninformative reviews: " + str(len(uninformRev)))

Average F-Score for the test data: 0.937800034927184
Number of informative reviews: 29813
Number of uninformative reviews: 17599
Wall time: 842 ms


In [4]:
listOfRemovedIndex_p3 = []

for i in range(0, len(uninformRev)):
    print(uninformRev[i].id)
    print(uninformRev[i].id - (len(trainSet) + len(testSet)))
    uninformRev[i].printSelf()
    print('\n')
    
    idxToRemove = uninformRev[i].id - (len(trainSet) + len(testSet))
    listOfRemovedIndex_p3.append(idxToRemove)

3603
89
Review id: 3603 Rating: 5 Content: app great also need review vehicl road Ntokens: 7 TS:  Group:  Prob: 0 label: 0
Raw text: app is great but you also need to review some vehicles that are on the road


3609
95
Review id: 3609 Rating: 5 Content: good occasion map issu especi chavchavadz vazha pshavela tbilisi Ntokens: 9 TS:  Group:  Prob: 0 label: 0
Raw text: very good with occasional map issues especially on chavchavadze and vazha pshavela tbilisi


3698
184
Review id: 3698 Rating: 4 Content: except comparison thank Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: exceptional no comparison with any other thanks


3706
192
Review id: 3706 Rating: 3 Content: lost item report still retriev uncomfort incid otherwis app cool Ntokens: 10 TS:  Group:  Prob: 0 label: 0
Raw text: i lost am item reported and still couldn t retrieve it very uncomfortable incidence otherwise this app is cool for me


3721
207
Review id: 3721 Rating: 5 Content: great experi custom satisfact orient applic

6941
3427
Review id: 6941 Rating: 5 Content: good use Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: it s very good and useful


6949
3435
Review id: 6949 Rating: 4 Content: great round experi Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: great all round experience


6959
3445
Review id: 6959 Rating: 5 Content: good servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: very good service


6961
3447
Review id: 6961 Rating: 5 Content: good servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: very good service


6965
3451
Review id: 6965 Rating: 5 Content: great app great ride Ntokens: 4 TS:  Group:  Prob: 0 label: 0
Raw text: great apps great rides


6968
3454
Review id: 6968 Rating: 5 Content: great experi everyday Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: great experience everyday


6969
3455
Review id: 6969 Rating: 5 Content: great servic right door step Ntokens: 5 TS:  Group:  Prob: 0 label: 0
Raw text: it s great service right at your door step


6970
3456

7859
Review id: 11373 Rating: 1 Content: scooter alway broken none choos Ntokens: 5 TS:  Group:  Prob: 0 label: 0
Raw text: scooters are always broken or there are none to choose from


11380
7866
Review id: 11380 Rating: 5 Content: never better thumb Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: never been better than this thumbs up


11384
7870
Review id: 11384 Rating: 5 Content: perfect Ntokens: 1 TS:  Group:  Prob: 0 label: 0
Raw text: it was perfect


11394
7880
Review id: 11394 Rating: 5 Content: good econom need continu improv Ntokens: 5 TS:  Group:  Prob: 0 label: 0
Raw text: its been good and economical just need continuous improvement


11396
7882
Review id: 11396 Rating: 4 Content: great ride Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: i had a great ride


11403
7889
Review id: 11403 Rating: 5 Content: love simplic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: i loving the simplicity


11406
7892
Review id: 11406 Rating: 4 Content: great servic quickli Ntoke

Review id: 11822 Rating: 5 Content: except good servic Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: exceptional good service


11823
8309
Review id: 11823 Rating: 5 Content: great transport app Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: great transportation app


11826
8312
Review id: 11826 Rating: 3 Content: often unrealist predict ariv time slowest one minut life Ntokens: 9 TS:  Group:  Prob: 0 label: 0
Raw text: often unrealistic predictions of arival time slowest one minute of my life


11834
8320
Review id: 11834 Rating: 5 Content: experi good Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: my experience very good


11835
8321
Review id: 11835 Rating: 5 Content: enjoy everyth app Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: i am enjoying everything about this app


11836
8322
Review id: 11836 Rating: 1 Content: worst app ever suppos pay end journey come hate Ntokens: 9 TS:  Group:  Prob: 0 label: 0
Raw text: the worst app ever when you are supposed to pay be


13253
9739
Review id: 13253 Rating: 3 Content: noth brag honestli happi take point b Ntokens: 7 TS:  Group:  Prob: 0 label: 0
Raw text: nothing i can brag about honestly just happy that it takes me from point a to b


13254
9740
Review id: 13254 Rating: 5 Content: good cool Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: good and cool


13255
9741
Review id: 13255 Rating: 4 Content: cool nice Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: cool nice


13256
9742
Review id: 13256 Rating: 3 Content: cool Ntokens: 1 TS:  Group:  Prob: 0 label: 0
Raw text: cool and smoot


13257
9743
Review id: 13257 Rating: 5 Content: realli awesom Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: it was really awesome


13258
9744
Review id: 13258 Rating: 5 Content: nice app good Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: nice apps good


13259
9745
Review id: 13259 Rating: 5 Content: r nice Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: they r very nice


13260
9746
Review id: 13260 

...

47994
44480
Review id: 47994 Rating: 5 Content: wonder servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: wonderful service


47996
44482
Review id: 47996 Rating: 5 Content: highli recommend great app great servic Ntokens: 6 TS:  Group:  Prob: 0 label: 0
Raw text: highly recommend great app great service


48000
44486
Review id: 48000 Rating: 5 Content: brilliant app absolut fantast Ntokens: 4 TS:  Group:  Prob: 0 label: 0
Raw text: brilliant app absolutely fantastic


48002
44488
Review id: 48002 Rating: 4 Content: good use Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: it s good and useful


48003
44489
Review id: 48003 Rating: 5 Content: great ride econom Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: great rides and economical


48004
44490
Review id: 48004 Rating: 5 Content: app amaz Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: this app is amazing


48005
44491
Review id: 48005 Rating: 5 Content: perfect Ntokens: 1 TS:  Group:  Prob: 0 label: 0
Raw text: is pe

48276
44762
Review id: 48276 Rating: 5 Content: fantast Ntokens: 1 TS:  Group:  Prob: 0 label: 0
Raw text: it s a fantastic


48278
44764
Review id: 48278 Rating: 4 Content: great app Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: great app


48279
44765
Review id: 48279 Rating: 5 Content: awesom app Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: awesome app


48280
44766
Review id: 48280 Rating: 5 Content: good app Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: good app


48293
44779
Review id: 48293 Rating: 1 Content: terribl manipul app steal inform tri pretend help viru Ntokens: 9 TS:  Group:  Prob: 0 label: 0
Raw text: terrible manipulative app steals information and tries to pretend it s helping virus


48295
44781
Review id: 48295 Rating: 1 Content: worst taxi applic ever use work bad dont use Ntokens: 9 TS:  Group:  Prob: 0 label: 0
Raw text: the worst taxi application ever used working very bad dont use it


48296
44782
Review id: 48296 Rating: 1 Content: shittiest

49565
46051
Review id: 49565 Rating: 5 Content: awesom servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: awesome service


49570
46056
Review id: 49570 Rating: 5 Content: suppos amaz way Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: does what it s supposed to in an amazing way


49571
46057
Review id: 49571 Rating: 5 Content: hi use mytaxi germani poland work perfect search cash swipe Ntokens: 10 TS:  Group:  Prob: 0 label: 0
Raw text: hi i used mytaxi in germany and poland and it works perfect no more searching for cash just swipe


49572
46058
Review id: 49572 Rating: 5 Content: great servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: great service


49575
46061
Review id: 49575 Rating: 5 Content: perfectli creat app Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: perfectly created app


49577
46063
Review id: 49577 Rating: 5 Content: perfect busi travel Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: perfect for business and other travelers


49578
46064
Re



49999
46485
Review id: 49999 Rating: 5 Content: nice help app love Ntokens: 4 TS:  Group:  Prob: 0 label: 0
Raw text: very nice and helpful app i love it


50007
46493
Review id: 50007 Rating: 5 Content: amaz app great featur great work Ntokens: 6 TS:  Group:  Prob: 0 label: 0
Raw text: amazing app with great features great work


50008
46494
Review id: 50008 Rating: 5 Content: good ride punctual Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: good ride and punctual


50022
46508
Review id: 50022 Rating: 3 Content: download size app phone need like Ntokens: 6 TS:  Group:  Prob: 0 label: 0
Raw text: 64mb is the download size for this app for my phone it needs 269mb why it is like that


50029
46515
Review id: 50029 Rating: 4 Content: good app hire person speak english Ntokens: 6 TS:  Group:  Prob: 0 label: 0
Raw text: good app but you should hire some such persons that can speak english


50034
46520
Review id: 50034 Rating: 5 Content: good user friendli Ntokens: 3 TS:  Group:  Pro


50713
47199
Review id: 50713 Rating: 5 Content: good app Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: good apps


50716
47202
Review id: 50716 Rating: 5 Content: first experi countri amaz Ntokens: 4 TS:  Group:  Prob: 0 label: 0
Raw text: first experience in my country was amazing d


50717
47203
Review id: 50717 Rating: 5 Content: grrrrreat Ntokens: 1 TS:  Group:  Prob: 0 label: 0
Raw text: grrrrreat


50720
47206
Review id: 50720 Rating: 4 Content: good app yerevan citi like Ntokens: 5 TS:  Group:  Prob: 0 label: 0
Raw text: good app in yerevan city i like it


50721
47207
Review id: 50721 Rating: 5 Content: work great tnx Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: it works great tnx


50723
47209
Review id: 50723 Rating: 5 Content: great better uber Ntokens: 3 TS:  Group:  Prob: 0 label: 0
Raw text: great better than uber


50724
47210
Review id: 50724 Rating: 1 Content: horribl servic Ntokens: 2 TS:  Group:  Prob: 0 label: 0
Raw text: horrible service


50731
47217
R

In [76]:
# listOfRemovedIndex_p3

In [8]:
%%time
df_p3 = df_p2.drop(df_p2.index[listOfRemovedIndex_p3])
total_reviews_before = len(df_p2)
total_reviews_after = len(df_p3)
total_removed_reviews = len(listOfRemovedIndex_p3)

print(f'Total reviews (BEFORE): {total_reviews_before} \n')
print(f'Total reviews (AFTER): {total_reviews_after} \n')
print(f'Total removed reviews: {total_removed_reviews} \n')

Total reviews (BEFORE): 47412 

Total reviews (AFTER): 29813 

Total removed reviews: 17599 

Wall time: 8.98 ms


In [9]:
df_p3.to_csv(config['csv_input_local']['all_reviews_p3'])

## Correcting Typos

In [42]:
%%time
cleaned_docs = remove_things(df_p3.review)
lists_of_words = list(sentences_to_words(cleaned_docs))
lists_of_words_no_stops = remove_stopwords(lists_of_words)
lists_of_words_no_stops

Wall time: 350 ms


[['using',
  'month',
  'good',
  'journeys',
  'horrendous',
  'ones',
  'recently',
  'first',
  'occasion',
  'told',
  'cross',
  'legs',
  'car',
  'might',
  'touch',
  'chair',
  'apparently',
  'encourages',
  'people',
  'sit',
  'still',
  'move',
  'car',
  'response',
  'got',
  'customer',
  'service',
  'refund',
  'second',
  'time',
  'dental',
  'appointment',
  'ordered',
  'cab',
  'driver',
  'came',
  'said',
  'going',
  'soon',
  'found',
  'location',
  'got',
  'frustrated',
  'swore',
  'said',
  'far',
  'man',
  'tired',
  'asked',
  'accepted',
  'first',
  'place',
  'want',
  'go',
  'far',
  'get',
  'proper',
  'explanation',
  'apology',
  'pain',
  'dental',
  'extraction',
  'cancel',
  'end',
  'said',
  'said',
  'would',
  'text',
  'let',
  'know',
  'messaged',
  'days',
  'ago',
  'still',
  'reply',
  'charged',
  'trip',
  'happen',
  'terrible',
  'terrible',
  'drivers',
  'bad',
  'customer',
  'service',
  'incidents',
  'like',
  'happen

In [49]:
list_of_typo_words = []
for sentence in lists_of_words_no_stops:
#     print(sentence)
    for word in sentence:
        if spell.correction(word) != word:
            print(word)
            print(spell.correction(word))
            list_of_typo_words.append(word)

xl
al
beckenham
beckham
cctv
cut
cctv
cut
deivers
drivers
fumingg
fuming
hru
thru
cornerr
corner
faq
far
kapten
kaiten
malta
malt
ffs
ifs
llocks
blocks
linkedin
linkedln
xx
ex
teip
trip
touran
toucan
tunis
tunes
gps
gas
viavan
vivian
ms
is
gps
gas
gps
gas
darkmode
darmody
usability
ability
gps
gas
viavan
vivian
postcodes
postcode
viavan
vivian
kapten
kaiten
gps
gas
slovakia
slovakian
kapten
kaiten
badd
bad
malta
malt
funke
funky
ms
is
funke
funky
meriza
media
londoner
londoners
btw
bow
gps
gas
аа
i
не
i
mr
my
masimba
marimba
pls
plus
befre
before
kapten
kaiten
xl
al
amaizing
amazing
kaunas
saunas
km
am
krakow
kraken
reaaly
really
latvia
latvian
ppl
pal
kapten
kaiten
gps
gas
gatwick
patrick
xs
is
xl
al
covid
couid
drivera
driver
kapten
kaiten
sh
so
ft
it
ft
it
ft
it
bmw
bow
tfl
til
sms
sums
unsubscribed
subscribed
uninstalled
installed
viavan
vivian
bonuss
bonus
nicee
nice
gps
gas
hrs
his
coudnt
count
happned
happened
muqtar
guitar
moalin
moulin
xl
al
xl
al
desaster
disaster
kaunas
saun

In [50]:
list_of_typo_words

['xl',
 'beckenham',
 'cctv',
 'cctv',
 'deivers',
 'fumingg',
 'hru',
 'cornerr',
 'faq',
 'kapten',
 'malta',
 'ffs',
 'llocks',
 'linkedin',
 'xx',
 'teip',
 'touran',
 'tunis',
 'gps',
 'viavan',
 'ms',
 'gps',
 'gps',
 'darkmode',
 'usability',
 'gps',
 'viavan',
 'postcodes',
 'viavan',
 'kapten',
 'gps',
 'slovakia',
 'kapten',
 'badd',
 'malta',
 'funke',
 'ms',
 'funke',
 'meriza',
 'londoner',
 'btw',
 'gps',
 'аа',
 'не',
 'mr',
 'masimba',
 'pls',
 'befre',
 'kapten',
 'xl',
 'amaizing',
 'kaunas',
 'km',
 'krakow',
 'reaaly',
 'latvia',
 'ppl',
 'kapten',
 'gps',
 'gatwick',
 'xs',
 'xl',
 'covid',
 'drivera',
 'kapten',
 'sh',
 'ft',
 'ft',
 'ft',
 'bmw',
 'tfl',
 'sms',
 'unsubscribed',
 'uninstalled',
 'viavan',
 'bonuss',
 'nicee',
 'gps',
 'hrs',
 'coudnt',
 'happned',
 'muqtar',
 'moalin',
 'xl',
 'xl',
 'desaster',
 'kaunas',
 'lyftt',
 'cs',
 'sms',
 'tallinn',
 'jdexgn',
 'cascais',
 'cascais',
 'mobey',
 'optionally',
 'cooll',
 'protus',
 'txfy',
 'huf',
 'huf',

## Processing Natural Language

In [56]:
df_p4 = df_p3.copy()
df_p4 = df_p4.reset_index(drop=True)
df_p4

userName  isEdited  \
0     Kazem Sharan     False   
1           19RN20     False   
2    evolvingihsan     False   
3         Sabcha08     False   
4        Ellenyh79     False   
..             ...       ...   
620      Vitaliy.l     False   
621       cretchen     False   
622  Nick_Name_Why     False   
623        Illimar     False   
624       kerdionu     False   

                                                review  rating  \
0    I’ve been using bolt for a month now. I had a ...       1   
1    I’m so appalled at the attitude of the last dr...       1   
2    I’ve had many problems with the customer suppo...       1   
3    So far majority of the drivers were very kind ...       3   
4    I was super happy when Bolt launch as finally ...       1   
..                                                 ...     ...   
620                                         Great app!       5   
621                                        Great app!!       5   
622  The drivers regularly get the wrong address du...       1   
623                                      Just love it!       5   
624                                         Great app!       5   

                                                 title                 date  
0                           Drivers are unprofessional  2019-09-20 09:25:04  
1                                          Zero Stars.  2020-09-04 19:50:50  
2                  HORRIBLE! HORRIBLE CUSTOMER SERVICE  2020-01-29 16:58:11  
3                                   Needs some updates  2019-07-05 12:17:37  
4    Terrible customer service and grossly overchar...  2019-10-03 22:17:44  
..                                                 ...                  ...  
620                                          Great app  2016-03-22 15:29:49  
621                                              Great  2015-07-14 20:13:38  
622                             Poor location accuracy  2019-10-08 10:57:34  
623                                         Perfect UX  2017-06-23 20:34:04  
624                                          Excellent  2015-08-04 18:18:57  

[625 rows x 6 columns]

### Coreference Resolution

In [51]:
import logging;
logging.basicConfig(level=logging.INFO)
import neuralcoref

# Load your usual SpaCy model (one of SpaCy English models)
import spacy
nlp = spacy.load('en')
# nlp = spacy.load("en_core_web_sm")

# Add neural coref to SpaCy's pipe
import neuralcoref
neuralcoref.add_to_pipe(nlp)

# You're done. You can now use NeuralCoref as you usually manipulate a SpaCy document annotations.
doc = nlp(u'My sister has a dog. She loves him.')
print(doc._.coref_resolved)

My sister has a dog. My sister loves a dog.


In [60]:
df_p4.review[1]

'I’m so appalled at the attitude of the last driver I ordered from you. Three people recommended your services and I trusted those opinions. I’ve only taken four trips with Bolt and not ONE driver has worn a mask including the trips taken with my 7 month old baby. I ordered a XL car to help with moving a mirror and a bassinet to my destination, he took 15 minutes to get here, was on a call via loud speaker with a friend/family member. I asked if I could put my stuff into the boot as I was moving house and collecting the last items I had at my previous home. He declined and the person he was speaking to on the phone also got involved also. He then said it was my fault for ordering the wrong type of car, I told him I ordered the biggest car option on bolt. He said I would have to find another car and then told ME to cancel the drive. I refused so as he drove off he shouted something and left me, my baby and my things in the cold. Then to make matters worse, he cancelled the trip and put 

In [61]:
for i in range(0, len(df_p4)):
    textToCheck = df_p4.review[i]
    doc = nlp(textToCheck)
    hasCoref = doc._.has_coref
    
    print(textToCheck)
    print('\n')
    print(hasCoref)
    
    if(hasCoref == True):
        print(doc._.coref_resolved)
        
    print('\n')
    

I’ve been using bolt for a month now. I had a few good journeys but 2 horrendous ones recently. The first occasion I was told to not cross my legs in the car because it “might” touch his chair. So apparently bolt encourages people to sit still and not move in the car, which was the response I got from customer service and no refund. The second time, I had a dental appointment and ordered a cab, the driver came and then he said where are you going? As soon as he found out what the location was, he got frustrated and swore and said “this is too far man I’m tired”. I asked why he had accepted it in the first place if he didn’t want to go too far. I didn’t get any proper explanation and no apology. I was in pain because of my dental extraction too. So I had to cancel from my end because he said he couldn’t do it. He said he would text bolt and let them know. And I messaged Bolt 3 days ago and still no reply. They have charged me £3 for this trip that didn’t happen. Terrible terrible driver

I was super happy when Bolt launch as finally there’s fair competition for taxi apps in London. After using it a couple of times I was happy. Until I took a ride from Beckenham to Heathrow I was quoted an estimate of £45-50. But after the ride I noticed that Bolt had charged me £87 instead!!! I contacted customer service and they have been absolutely USELESS!! It’s been 2 weeks and I’m going round in circles with them asking me again what my route was, how much I was charged, sending them bank statements. They have refused to acknowledge the overcharge and not giving refund. If I had known they were going to charge such extortionate price I would have hired a local minicab company or gone with Uber instead! If I had raised such issue with Uber there would be an immediate refund. Watch out for these scammers!


True
I was super happy when Bolt launch as finally there’s fair competition for taxi apps in London. After using it a couple of times I was happy. Until I took a ride from Becken

So I’m trying out Bolt as a potential alternative to Uber, given the situation with Uber in London. Prices are good but Bolt needs to do a bit of work on the app!
1. The idea of being able to modify the pick up location should be added. You have to cancel and start agin even just for crossing the road
2. Being able to track the potential route would be useful, especially if you’re familiar with the route and can suggest modifications
Still - great to have an alternative to Uber! And drivers are all good too so far


True
So I’m trying out Bolt as a potential alternative to Uber, given the situation with Uber in London. Prices are good but Bolt needs to do a bit of work on the app!
1. The idea of being able to modify the pick up location should be added. You have to cancel and start agin even just for crossing the road
2. Being able to track the potential route would be useful, especially if you’re familiar with the route and can suggest modifications
Still - great to have an alternativ

Used three times so far after good friend recommended and send me invite that gave me good welcome discount which was plus! Overall professional drivers and friendly drivers. New or very decent cars and very quick pick up which was very great first impression. Keep up the good work!


False


Having used Uber for years and made over 1000 trips, I decided to try Bolt.
Cost wise it was extremely heap the first few rides, but now it is almost always more than Uber for the same route.
The app is very inaccurate and doesn’t recognise places of interest at all. I always have to message the driver to explain exactly where I am.
The app could definitely benefit from more development on the location accuracy.


True
Having used Uber for years and made over 1000 trips, I decided to try Bolt.
Cost wise it was extremely heap the first few rides, but now it is almost always more than Uber for the same route.
The app is very inaccurate and doesn’t recognise places of interest at all. I always have t

Nice service. Getting promotions from time to time. But the only thing that is lacking - two address request. It’s very common service. Instead of minimize communication with drivers, we need to explain that we would change final destination when we come closer to first one. So that driver won’t take next trip. Confusing.


True
Nice service. Getting promotions from time to time. But the only thing that is lacking - two address request. the only thing that is lacking - two address request’s very common service. Instead of minimize communication with drivers, we need to explain that we would change final destination when we come closer to first one. So that driver won’t take next trip. Confusing.


First trip was ok, second time I booked a trip, the app told me 8 min waiting time, the driver called me and said he would be 15 mins not 8 mins and did I want to cancel, I said no I would wait, after 15 mins waiting the driver cancelled the trip, after that I couldn’t not get another bolt ri

...

It’s good application.i have been used this app in Kaunas,Lithuania for 2-3 months .some of the driver can speak English and most of them are not speak English.some driver always took a longer route even it shows up on their equipment.i try to explain to them but seem like they don’t care and end up my payment was higher than expected.

I tried to contract bolt application service but it’s so difficult ,the only way for you to contact them is to email them.
No live chat 

the good things that you can shared your journey with another person.


True
It’s good application.i have been used this app in Kaunas,Lithuania for 2-3 months .some of the driver can speak English and most of them are not speak English.some driver always took a longer route even a longer route shows up on them equipment.i try to explain to them but seem like them don’t care and end up my payment was higher than expected.

I tried to contract bolt application service but a longer route’s so difficult ,the only way for

App is terrible. In the login process I'm supposed to receive SMS with login code. I've tried to enter my phone number for a number of times and nothing. I'm not receiving message with login code. Also, even worse... I needed a ride when it was heavy rain outside. Terrible service.


True
App is terrible. In the login process I'm supposed to receive SMS with login code. I've tried to enter my phone number for a number of times and nothing. I'm not receiving message with login code. Also, even worse... I needed a ride when a ride was heavy rain outside. Terrible service.


Worst taxi app in world. I got called dirty words so many times, harassed sexually and now they started to charge my card without even using it. I am getting transactions with “Tallinn/Bolt.eu” and I didn’t use this crap for several days. THIS IS PURE SCAM and must be removed from iTunes


True
Worst taxi app in world. I got called dirty words so many times, harassed sexually and now they started to charge my card wit

I took a ride in for 4070 HUF. The company charged me 407000 HUF. I can’t believe that this was mistake!! I was surprised to see -1333 EUR when checked my bank account. The support not answering to the messages. Not possible to join anyone by phone. The drivers are taking longer routes to charge you more. By far the worst taxi app you can imagine !!! Use Uber and you’d save yourself a lot of trouble. 0 stars for Taxify in every way.
#Update 28/12: Taxify blocked my number after this review. Well done because I don’t want  to hear about you anymore and that confirms the unprofessional methods of this company !!


True
I took a ride in for 4070 HUF. 4070 HUF charged me 407000 HUF. I can’t believe that this was mistake!! I was surprised to see -1333 EUR when checked my bank account. The support not answering to the messages. Not possible to join anyone by phone. The drivers are taking longer routes to charge you more. By far the worst taxi app you can imagine !!! Use Uber and you’d save y

Just signed up, they charged me with 2 euros and the bike didn’t move at all. Maybe the device was broken, I don’t know. But I didn’t use the bike and I had to pay for a trip.


True
Just signed up, they charged me with 2 euros and the bike didn’t move at all. Maybe the device was broken, I don’t know. But I didn’t use the bike and I had to pay for a trip.


BOLT is the worst ride sharing app I have ever tried. It took my money twice and I’ve never had a trip yet, this is unbelievable and has to be stopped. They are thieves and have to be removed from the market.


True
BOLT is the worst ride sharing app I have ever tried. app took my money twice and I’ve never had a trip yet, this is unbelievable and has to be stopped. They are thieves and have to be removed from the market.


It took more than 20 minutes for our ride to get to our destination, once it was close, it stated that it was finishing another ride and was going to take another 10 minutes. After I cancel the ride the app char



True
A very helpful app, but why I can't just watch the list of taxi companies with taxi companies phonenumbers?


Its fine.


False


BEST app ever! So easy to use and very functional!


False


Great app! Works perfectly.


False


Shows 1 min. Taxi arrives in 9min. Shows 3 min. Taxi arrives in 6 min etc.


True
Shows 1 min. Taxi arrives in 9min. Shows 3 min. Taxi arrives in 6 min etc.


Good app. I suggest


False


Very good and helpful app!


False


Great app!


False


Superb app! Thanks devs!!


False


Great app!


False


Great app!!


False


The drivers regularly get the wrong address due to some poor auto-replacement-with-the-local-hotspot function even though to the customer the app displays their correct address. Which leads the customer to blame the unsuspecting driver who can’t do anything about it. Bolt, your customer experience sucks!


True
The drivers regularly get the wrong address due to some poor auto-replacement-with-the-local-hotspot function even though to 

### Sentence Annotation

In [ ]:
# TODO

## Building Corpus

In [62]:
df_p5 = df_p4.copy()
df_p5

userName  isEdited  \
0     Kazem Sharan     False   
1           19RN20     False   
2    evolvingihsan     False   
3         Sabcha08     False   
4        Ellenyh79     False   
..             ...       ...   
620      Vitaliy.l     False   
621       cretchen     False   
622  Nick_Name_Why     False   
623        Illimar     False   
624       kerdionu     False   

                                                review  rating  \
0    I’ve been using bolt for a month now. I had a ...       1   
1    I’m so appalled at the attitude of the last dr...       1   
2    I’ve had many problems with the customer suppo...       1   
3    So far majority of the drivers were very kind ...       3   
4    I was super happy when Bolt launch as finally ...       1   
..                                                 ...     ...   
620                                         Great app!       5   
621                                        Great app!!       5   
622  The drivers regularly get the wrong address du...       1   
623                                      Just love it!       5   
624                                         Great app!       5   

                                                 title                 date  
0                           Drivers are unprofessional  2019-09-20 09:25:04  
1                                          Zero Stars.  2020-09-04 19:50:50  
2                  HORRIBLE! HORRIBLE CUSTOMER SERVICE  2020-01-29 16:58:11  
3                                   Needs some updates  2019-07-05 12:17:37  
4    Terrible customer service and grossly overchar...  2019-10-03 22:17:44  
..                                                 ...                  ...  
620                                          Great app  2016-03-22 15:29:49  
621                                              Great  2015-07-14 20:13:38  
622                             Poor location accuracy  2019-10-08 10:57:34  
623                                         Perfect UX  2017-06-23 20:34:04  
624                                          Excellent  2015-08-04 18:18:57  

[625 rows x 6 columns]

In [64]:
cleaned_docs = remove_things(df_p5.review)
lists_of_words = list(sentences_to_words(cleaned_docs))
lists_of_words_no_stops = remove_stopwords(lists_of_words)

ngrams = make_bigrams(lists_of_words_no_stops)
# ngrams = make_trigrams(lists_of_words_no_stops)

data_lemmatized = lemmatize(ngrams, allowed_postags=['NOUN'])

Making bigrams...
Lemmatizing...


In [65]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
term_doc = [id2word.doc2bow(text) for text in texts]

# View
print(term_doc[:1])

[[(0, 1), (1, 1), (2, 2), (3, 1), (4, 1), (5, 1), (6, 2), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1)]]


In [67]:
tf_idf = models.TfidfModel(term_doc, smartirs='ntc')[term_doc]
[[(id2word[id], freq) for id, freq in cp] for cp in tf_idf[:1]]

[[('apology', 0.258303175195304),
  ('appointment', 0.19374341386795016),
  ('car', 0.1660609726432199),
  ('chair', 0.258303175195304),
  ('cross', 0.2304987993967995),
  ('day', 0.12187014507285714),
  ('driver', 0.07236556805706493),
  ('explanation', 0.2304987993967995),
  ('extraction', 0.258303175195304),
  ('incident', 0.2142342821987155),
  ('journey', 0.12323004598478411),
  ('leg', 0.258303175195304),
  ('location', 0.1423610134036225),
  ('man', 0.19374341386795016),
  ('month', 0.19374341386795016),
  ('occasion', 0.20269442359829498),
  ('one', 0.18642990640021098),
  ('pain', 0.258303175195304),
  ('people', 0.15244204814412854),
  ('place', 0.18024642394263304),
  ('refund', 0.14019220224671175),
  ('response', 0.15244204814412854),
  ('swore', 0.258303175195304),
  ('text', 0.258303175195304),
  ('trip', 0.10301677900469748)]]

In [73]:
with open(config['csv_input_local']['bolt_apple_corpus'], 'wb') as f:
    pickle.dump(tf_idf, f)

# Creating Pickle File For Topic Modelling

In [11]:
all_reviews_p3 = pd.read_csv(config['csv_input_local']['all_reviews_p3'], index_col=0)
all_reviews_p3 = all_reviews_p3.reset_index(drop=True)
all_reviews_p3

userName                                             review  \
0          Hilary Meyer  Your drivers are great BUT your support is no ...   
1             Kenneth B  Loving the app, but can only give it a medium ...   
2      Bonolo Mphahlele  The response time with regards to customer ser...   
3       jessfechi egolo  This has been happening for some time now and ...   
4         Safeeya Lawal  The drivers almost always never have change an...   
...                 ...                                                ...   
29808         P.Raimond  It’s rather difficult to get a taxi. Sometimes...   
29809    sõidan taksoga  Taxi drivers don’t speak Estonian or English. ...   
29810         madsp1r1t  Ride booking extension in Apple maps not avail...   
29811           hmerith  I ordered a taxi, but when it arrived the driv...   
29812     lalalaaalalaa  taxis are always late without exception. drive...   

       rating                 date  
0           3  2020-12-06 19:38:13  
1           3  2020-12-11 14:06:15  
2           4  2020-12-07 13:59:18  
3           1  2020-12-13 18:19:06  
4           3  2020-12-05 15:08:10  
...       ...                  ...  
29808       3  2018-05-30 05:37:16  
29809       1  2018-11-11 10:32:50  
29810       3  2019-11-07 18:53:33  
29811       1  2019-07-12 23:33:57  
29812       1  2020-11-07 15:30:33  

[29813 rows x 4 columns]

In [12]:
df_merged = all_reviews_p3.review.astype(str)
df_merged

0        Your drivers are great BUT your support is no ...
1        Loving the app, but can only give it a medium ...
2        The response time with regards to customer ser...
3        This has been happening for some time now and ...
4        The drivers almost always never have change an...
                               ...                        
29808    It’s rather difficult to get a taxi. Sometimes...
29809    Taxi drivers don’t speak Estonian or English. ...
29810    Ride booking extension in Apple maps not avail...
29811    I ordered a taxi, but when it arrived the driv...
29812    taxis are always late without exception. drive...
Name: review, Length: 29813, dtype: object

In [15]:
cleaned_docs = remove_things(df_merged)

lists_of_words = list(sentences_to_words(cleaned_docs))
lists_of_words_no_stops = remove_stopwords(lists_of_words)

ngrams = make_bigrams(lists_of_words_no_stops)

data_lemmatized = lemmatize(ngrams, allowed_postags=['NOUN'])

# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
term_doc = [id2word.doc2bow(text) for text in texts]

# View
print(term_doc[:1])

tf_idf = models.TfidfModel(term_doc, smartirs='ntc')[term_doc]
tf_idf[0]

Making bigrams...
Lemmatizing...
[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 2), (7, 2), (8, 1)]]


[(0, 0.21958462805603177),
 (1, 0.26862676361814714),
 (2, 0.27642847383644364),
 (3, 0.4245728933893095),
 (4, 0.22483537349158902),
 (5, 0.06450706409796483),
 (6, 0.47150660756895796),
 (7, 0.4692008422840324),
 (8, 0.35463698646382735)]

In [17]:
import pickle
output_path = 'preprocessed_data/all/'

with open(output_path + 'data_lemmatized.pkl', 'wb') as f:
    pickle.dump(data_lemmatized, f)
    
with open(output_path + 'dictionary.pkl', 'wb') as f:
    pickle.dump(id2word, f)
    
with open(output_path + 'term_doc.pkl', 'wb') as f:
    pickle.dump(term_doc, f)
    
with open(output_path + 'tf_idf.pkl', 'wb') as f:
    pickle.dump(tf_idf, f)